# Fish Speech

### For Windows User / win用户

In [ ]:
!chcp 65001

### For Linux User / Linux 用户

In [1]:
import locale
locale.setlocale(locale.LC_ALL, 'en_US.UTF-8')

'en_US.UTF-8'

### Prepare Model

In [2]:
# For Chinese users, you probably want to use mirror to accelerate downloading
# !set HF_ENDPOINT=https://hf-mirror.com
# !export HF_ENDPOINT=https://hf-mirror.com 

# !huggingface-cli download fishaudio/fish-speech-1.5 --local-dir checkpoints/fish-speech-1.5/

## WebUI Inference

> You can use --compile to fuse CUDA kernels for faster inference (10x).

In [ ]:
!python tools/run_webui.py \
    --llama-checkpoint-path checkpoints/fish-speech-1.5 \
    --decoder-checkpoint-path checkpoints/fish-speech-1.5/firefly-gan-vq-fsq-8x1024-21hz-generator.pth \
    # --compile

## Break-down CLI Inference

### 1. Encode reference audio: / 从语音生成 prompt: 

You should get a `fake.npy` file.

你应该能得到一个 `fake.npy` 文件.

In [ ]:
# Enter the path to the audio file here
!python fish_speech/models/vqgan/inference.py \
    -i ./Surtr-001.ogg \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/firefly-gan-vq-fsq-8x1024-21hz-generator.pth"

/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/lookup_free_quantization.py:209: FutureWarning: `torch.cuda.amp.autocast(args...)

In [6]:
from IPython.display import Audio, display
audio = Audio(filename="fake.wav")
display(audio)

### 2. Generate semantic tokens from text: / 从文本生成语义 token:

> This command will create a codes_N file in the working directory, where N is an integer starting from 0.

> You may want to use `--compile` to fuse CUDA kernels for faster inference (~30 tokens/second -> ~300 tokens/second).

> 该命令会在工作目录下创建 codes_N 文件, 其中 N 是从 0 开始的整数.

> 您可以使用 `--compile` 来融合 cuda 内核以实现更快的推理 (~30 tokens/秒 -> ~300 tokens/秒)

In [12]:
!python fish_speech/models/text2semantic/inference.py \
    --text "他人の指導役はもうごめんだ。一般人たちと雁首揃えてアーツごっこするなんて興味ない。" \
    --prompt-text "あんた、自分の仕事も全うできないからって、私に助けろっていうの？" \
    --prompt-tokens "fake.npy" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/" \
    --num-samples 3
    # --compile

2025-04-19 23:44:05.579 | INFO     | __main__:main:1056 - Loading model ...
2025-04-19 23:44:10.358 | INFO     | __main__:load_model:681 - Restored model from checkpoint
2025-04-19 23:44:10.358 | INFO     | __main__:load_model:687 - Using DualARTransformer
2025-04-19 23:44:10.367 | INFO     | __main__:main:1070 - Time to load model: 4.79 seconds
starting generation
2025-04-19 23:44:10.378 | INFO     | __main__:generate_long:788 - Encoded text: 他人の指導役はもうごめんだ。
2025-04-19 23:44:10.381 | INFO     | __main__:generate_long:788 - Encoded text: 一般人たちと雁首揃えてアーツごっこするなんて興味ない。
2025-04-19 23:44:10.381 | INFO     | __main__:generate_long:806 - Generating sentence 1/2 of sample 1/3
  0%|                                                  | 0/8001 [00:00<?, ?it/s]/home/sam/miniconda3/envs/fish-speech/lib/python3.10/contextlib.py:103: FutureWarning: `torch.backends.cuda.sdp_kernel()` is deprecated. In the future, this context manager will be removed. Please see `torch.nn.attention.sdpa_kernel()` for the n

### 3. Generate speech from semantic tokens: / 从语义 token 生成人声:

In [24]:
!python fish_speech/models/vqgan/inference.py \
    -i "./temp_0/codes_0.npy" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/firefly-gan-vq-fsq-8x1024-21hz-generator.pth"

from IPython.display import Audio, display
audio = Audio(filename="fake.wav")
display(audio)

/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/lookup_free_quantization.py:209: FutureWarning: `torch.cuda.amp.autocast(args...)

In [ ]:
# 305152 / 149 = 2048

In [ ]:
!python fish_speech/models/vqgan/inference.py \
    -i "./temp_0/codes_1.npy" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/firefly-gan-vq-fsq-8x1024-21hz-generator.pth"

from IPython.display import Audio, display
audio = Audio(filename="fake.wav")
display(audio)

/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/lookup_free_quantization.py:209: FutureWarning: `torch.cuda.amp.autocast(args...)

In [ ]:
# 282624 / 138 = 2048

In [ ]:
!python fish_speech/models/vqgan/inference.py \
    -i "./temp_0/codes_2.npy" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/firefly-gan-vq-fsq-8x1024-21hz-generator.pth"

from IPython.display import Audio, display
audio = Audio(filename="fake.wav")
display(audio)

/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/lookup_free_quantization.py:209: FutureWarning: `torch.cuda.amp.autocast(args...)

In [ ]:
# 313344 / 153 = 2048

In [26]:
!python fish_speech/models/vqgan/inference.py \
    -i "./temp_0/codes_3.npy" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/firefly-gan-vq-fsq-8x1024-21hz-generator.pth"

from IPython.display import Audio, display
audio = Audio(filename="fake.wav")
display(audio)

/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/lookup_free_quantization.py:209: FutureWarning: `torch.cuda.amp.autocast(args...)

In [ ]:
# 344064 / 168 = 2048

In [ ]:
# so i'm currently using fish speech 1.5, and i'm trying to think of a way to get real time streaming. currently there's two main components. the llm that takes in text + audio tokens, and outputs audio tokens, and there's also a GAN decoder that takes in those audio tokens and generates a .wav file from it. the GAN decoding process takes like 0.2 seconds, whereas the LLM decoding needs 3+ seconds (definitely the bottleneck). 
# currently the system waits until the LLM decoding finishes before moving on to the GAN decoding, which makes sense, as if you lets say have a paragraph that you want to generate audio tokens for, the tone in the later parts of the paragraph can be highly dependent on the earlier parts of the paragraph, so it makes sense to wait until all the audio tokens are generated, before doing the GAN decoding. the issue is that this prevents real time output. the only way i can think of getting real time audio generation is by going sentence by sentence or something, but that doesn't feel great. 
# or... i'm not sure how exactly it's done, but assuming it's like eva-gan, (though slightly different, since eva gan takes in mel spectogram histogram bins, whereas this GAN decoder takes in latent vectors), and one token always maps up through 1d transposed convolutions to always the same amount of time in output seconds, then you might be able to pass in overlapping chunks of audio tokens to the GAN, and just calculate the locations to splice together the audio generations?



# ok yeah. seems like it is like eva-gan with 1d convs and fixed upscaling. numerator is audio shape[0], and denominator is token shape[0]# 305152 / 149 = 2048
# 282624 / 138 = 2048
# 313344 / 153 = 2048
# i think the overlapping chunk idea might work



# or maybe even. if the gan generation time scales significantly better than the token generation time, might be worth just passing in all previous tokens in along with the 100 new tokens, and send the spliced 100 new tokens to the client. (?)
# might be worth me testing on already generated indices, and just do a cumsum kinda generations, and see if the idea even works in the first place in terms of quality and speed.

# going to make an INFERENCE CUM file in the vqgan folder



In [42]:
!python fish_speech/models/vqgan/inference_cum.py \
    -i "./temp_0/codes_2.npy" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/firefly-gan-vq-fsq-8x1024-21hz-generator.pth"

from IPython.display import Audio, display
audio = Audio(filename="shit.wav")
display(audio)

/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/lookup_free_quantization.py:209: FutureWarning: `torch.cuda.amp.autocast(args...)

In [ ]:
# combine together audio files. 
from pydub import AudioSegment
import os

wavs = list(map(lambda x: f"./temp0/{x}", sorted(list(filter(lambda x: x.startswith("new"), os.listdir("./temp"))), key=lambda x: int(x.split(".")[0].split("-")[1]))))

combined = AudioSegment.empty()
for wav in wavs:
  print(wav)
  audio = AudioSegment.from_wav(wav)
  combined += audio  # Append

combined.export("combined_output.wav", format="wav")

from IPython.display import Audio, display
audio = Audio(filename="combined_output.wav")
display(audio)

./temp/new-10.wav
./temp/new-20.wav
./temp/new-30.wav
./temp/new-40.wav
./temp/new-50.wav
./temp/new-60.wav
./temp/new-70.wav
./temp/new-80.wav
./temp/new-90.wav
./temp/new-100.wav
./temp/new-110.wav
./temp/new-120.wav
./temp/new-130.wav
./temp/new-140.wav
./temp/new-150.wav
./temp/new-153.wav


In [ ]:
# OK YEP. IT WORKS. splicing it together works!

# ok yep. i think it actually works. guess the vq-vae codebook for the decoder/encoder gan actually maps pretty consistently to the same sound, even when considering cross-context in gan. i don't even need to do any processing afterwards. just the raw spliced wav files, can be recombined. 

# i guess to check the codebook mapping idea, i can remove prior context for the gan generation and see if the audio still matches up.

In [34]:
!python fish_speech/models/vqgan/inference_cum.py \
    -i "./temp_0/codes_2.npy" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/firefly-gan-vq-fsq-8x1024-21hz-generator.pth"

/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/lookup_free_quantization.py:209: FutureWarning: `torch.cuda.amp.autocast(args...)

In [1]:
# combine together audio files. 
from pydub import AudioSegment
import os

wavs = list(map(lambda x: f"./temp_0/{x}", sorted(list(filter(lambda x: x.startswith("ONLYnew"), os.listdir("./temp"))), key=lambda x: int(x.split(".")[0].split("-")[1]))))

combined = AudioSegment.empty()
for wav in wavs:
  print(wav)
  audio = AudioSegment.from_wav(wav)
  combined += audio  # Append

combined.export("combined_output-2.wav", format="wav")

from IPython.display import Audio, display
audio = Audio(filename="combined_output-2.wav")
display(audio)

./temp/ONLYnew-10.wav
./temp/ONLYnew-20.wav
./temp/ONLYnew-30.wav
./temp/ONLYnew-40.wav
./temp/ONLYnew-50.wav
./temp/ONLYnew-60.wav
./temp/ONLYnew-70.wav
./temp/ONLYnew-80.wav
./temp/ONLYnew-90.wav
./temp/ONLYnew-100.wav
./temp/ONLYnew-110.wav
./temp/ONLYnew-120.wav
./temp/ONLYnew-130.wav
./temp/ONLYnew-140.wav
./temp/ONLYnew-150.wav
./temp/ONLYnew-153.wav


In [ ]:
# VERY INTERESTING. THERE ARE ARTIFACTS WITHOUT LOOKING AT PRIOR CONTEXT. 

# OK very interesting. the prior context for the GAN does matter. without it, it still sounds pretty decent, but there are moments where the audio cuts out or has a very abrupt transition. rather amusing to think about. the earlier audio portions don't seem to be affected much if at all by later portions, but later portions are affected quite heavily by earlier portions. 
# considering the "multi-receptive fields" for the convolutions going on, i would've imagined that earlier upsamples would look ahead towards later audio tokens and be notably informed by it. guess it's not a significant effect.

In [ ]:
# testing inference cum method for dual ar llm system

# https://arknights.wikiru.jp/?%E3%82%B9%E3%83%AB%E3%83%88#voice
!python fish_speech/models/text2semantic/inference_cum.py \
    --text "他人の指導役はもうごめんだ。一般人たちと雁首揃えてアーツごっこするなんて興味ない。" \
    --prompt-text "あんた、自分の仕事も全うできないからって、私に助けろっていうの？" \
    --prompt-tokens "surtr.npy" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/" \
    --num-samples 1
    # --compile

2025-04-20 06:04:13.077 | INFO     | __main__:main:1197 - Loading model VQGAN ...
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch

In [1]:
# testing inference cum method for dual ar llm system

# https://arknights.wikiru.jp/?%E3%82%B9%E3%83%AB%E3%83%88#voice
!python fish_speech/models/text2semantic/inference_cum.py \
    --text "他人の指導役はもうごめんだ。一般人たちと雁首揃えてアーツごっこするなんて興味ない。" \
    --prompt-text "あんた、自分の仕事も全うできないからって、私に助けろっていうの？" \
    --prompt-tokens "surtr.npy" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/" \
    --num-samples 1
    # --compile

2025-04-21 00:05:23.750 | INFO     | __main__:main:1197 - Loading model VQGAN ...
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch

In [22]:
# testing inference cum method for dual ar llm system

    # --text "他人の指導役はもうごめんだ。一般人たちと雁首揃えてアーツごっこするなんて興味ない。" \
    # --prompt-text "あんた、自分の仕事も全うできないからって、私に助けろっていうの？" \
    # --prompt-tokens "surtr.npy" \
    # --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/" \
# https://arknights.wikiru.jp/?%E3%82%B9%E3%83%AB%E3%83%88#voice
!python fish_speech/models/text2semantic/inference_cum_api.py \
    --checkpoint-path /media/sam/pain/models/fishaudio/fish-speech-1.5/ \
    --output-base-dir ./output/temp \
    --no-compile

Namespace(checkpoint_path='/media/sam/pain/models/fishaudio/fish-speech-1.5/', device='cuda', compile=False, output_base_dir='./output/temp', half=False)
sanity check
2025-04-21 01:23:19.532 | INFO     | __main__:<module>:95 - Loading VQGAN ...
2025-04-21 01:23:20.078 | INFO     | __main__:load_model_vqgan:91 - Loaded model: <All keys matched successfully>
2025-04-21 01:23:20.078 | INFO     | __main__:<module>:102 - Loaded VQGAN in 0.546730
2025-04-21 01:23:20.084 | INFO     | __main__:<module>:1215 - Loading model LLM ...
2025-04-21 01:23:24.508 | INFO     | __main__:load_model_llm:888 - Restored model from checkpoint
2025-04-21 01:23:24.508 | INFO     | __main__:load_model_llm:894 - Using DualARTransformer
2025-04-21 01:23:24.516 | INFO     | __main__:<module>:1229 - Time to load model: 4.43 seconds
Starting server... Imports loaded.
INFO:     Started server process [38148]
INFO:     Waiting for application startup.
INFO:     Application startup complete.
ERROR:    [Errno 98] error w

In [33]:
# testing inference cum method for dual ar llm system

    # --text "他人の指導役はもうごめんだ。一般人たちと雁首揃えてアーツごっこするなんて興味ない。" \
    # --prompt-text "あんた、自分の仕事も全うできないからって、私に助けろっていうの？" \
    # --prompt-tokens "surtr.npy" \
    # --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/" \
# https://arknights.wikiru.jp/?%E3%82%B9%E3%83%AB%E3%83%88#voice
# !python fish_speech/models/text2semantic/inference_cum_api.py \
#     --checkpoint-path /media/sam/pain/models/fishaudio/fish-speech-1.5/ \
#     --output-base-dir ./output/temp \
#     --no-compile

!python fish_speech/models/text2semantic/inference_cum_api.py \
  --checkpoint-path /media/sam/pain/models/fishaudio/fish-speech-1.5/ \
  --compile

Namespace(checkpoint_path='/media/sam/pain/models/fishaudio/fish-speech-1.5/', device='cuda', compile=True, output_base_dir='./output', half=False)
2025-04-21 21:31:00.988 | INFO     | __main__:<module>:68 - Loading VQGAN ...
2025-04-21 21:31:01.655 | INFO     | __main__:load_model_vqgan:64 - Loaded model: <All keys matched successfully>
2025-04-21 21:31:01.656 | INFO     | __main__:<module>:75 - Loaded VQGAN in 0.667742
2025-04-21 21:31:01.662 | INFO     | __main__:main:1196 - Loading model ...
2025-04-21 21:31:06.060 | INFO     | __main__:load_model:846 - Restored model from checkpoint
2025-04-21 21:31:06.061 | INFO     | __main__:load_model:852 - Using DualARTransformer
2025-04-21 21:31:06.061 | INFO     | __main__:load_model:860 - Compiling function...
2025-04-21 21:31:06.684 | INFO     | __main__:main:1210 - Time to load model: 5.02 seconds
starting generation
2025-04-21 21:31:06.699 | INFO     | __main__:generate_long:953 - Encoded text: 真让人怀念，很多年前，我也曾如今天这般走入那谋臣似雨的阁楼。
2025-04-21 

In [54]:
!python fish_speech/models/vqgan/inference.py \
    -i "./voice/chen/aceship/CN_010.mp3" \
    --checkpoint-path "/media/sam/pain/models/fishaudio/fish-speech-1.5/firefly-gan-vq-fsq-8x1024-21hz-generator.pth"

/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:445: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/vector_quantize_pytorch.py:630: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/finite_scalar_quantization.py:147: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  @autocast(enabled = False)
/home/sam/miniconda3/envs/fish-speech/lib/python3.10/site-packages/vector_quantize_pytorch/lookup_free_quantization.py:209: FutureWarning: `torch.cuda.amp.autocast(args...)